# <center>ディープラーニング入門</center>
# <center>A LSTM in Wonderland</center>


In [22]:

import os
os.environ["CUDA_VISIBLE_DEVICES"]="2"
import tensorflow as tf
physical_devices = tf.config.experimental.list_physical_devices('GPU')
tf.config.experimental.set_memory_growth(physical_devices[0], True)


In [23]:
import numpy as np

# 1. 文字単位での文章生成

今回はLSTMで文章生成してみます。Kerasのexampleを少し改造したモデルを用意しました。

## 1-1. テキストデータのクリーニング

青空文庫から不思議の国のアリスのテキストファイルをダウンロードしましょう。

https://www.aozora.gr.jp/cards/001393/card57320.html

解凍したファイルのうち、alicewa_fushigino_kunide.txtをGoogle Driveのaliceフォルダに入れておきます。

In [67]:
file_path = './text/alicewa_fushigino_kunide.txt'
    
with open(file_path, 'r', encoding='shift-jis') as text_file:
    strings = text_file.read()
    
paras = strings.splitlines()

開いたテキストを見てみます：

In [68]:
# !cp ../../dm_integration/data/EPG_checking\ 0212_check.xlsx ./
!ls

A_thousand_ball_drill1202.ipynb  EPG.xlsx  output  text


In [69]:
import pandas as pd

In [70]:
df = pd.read_excel("./EPG.xlsx")

['ついにバディ結成で最初の事件に挑む!新宿駅で死んだ女は別人に成り代わった女だった…。“ディーン"シャーロックが対峙するのは、美しき弁護士・菅野美穂!天才が唯一惚れた特別な聖女との息詰まる心理戦が開幕!オリンピックを翌年に控えたTOKYOの街を舞台に、現代の日本に生まれ変わった世界一有名なバディ〈シャーロック=誉獅子雄×ワトソン=若宮潤一〉が、数々の難事件の謎に立ち向かうミステリーエンタテインメント上の階からの水漏れにより宿無しとなった誉獅子雄(ディーン・フジオカ)は、医師の転落死を巡る事件で知り合った若宮潤一(岩田剛典)のマンションに転がり込んだ。そんな中、捜査一課の江藤礼二(佐々木蔵之介)から獅子雄のもとへ新たな捜査依頼が舞い込んでくる。それはとある女性が急行電車にはねられ死亡した一件。所有していた身分証から亡くなったのは29歳の高橋博美だと判明する。博美はかつて、とあるトラブルを抱えており、敏腕弁護士の青木藍子(菅野美穂)に弁護の依頼をしていた。藍子は、依頼を受けた人にはたとえ弁護が終わっても一生寄り添うことをポリシーとする弁護士であり、生きづらさを抱える人々に対しグループワークを開くなど、社会的弱者の側に立った活動を一貫して続けている人格者。そんな藍子と博美の関係を知った獅子雄は、調査目的で藍子のもとを訪ねる。そこで獅子雄は弁護士としても女性としても完璧な藍子に興味を抱き…。',
 'オリンピックを翌年に控えたTOKYOの街を舞台に、現代の日本に生まれ変わった世界一有名なバディ〈シャーロック=誉獅子雄×ワトソン=若宮潤一〉が、数々の難事件の謎に立ち向かうミステリーエンタテインメント!今回のテーマは、地面師詐欺!巨額不動産を巡り詐欺師との息詰まる騙し合いが展開!そして殺された詐欺師が残したダイイングメッセージを解け!現場に残された長・短・短の3本の枝の謎!終わらないどんでん返し!渋谷の一等地にある空き家で、身元不明の高齢男性の死体が発見された。そこは5年前に巨額の地面師詐欺の舞台になった邸宅。事件後、詐欺被害にあった建設会社の社長がその邸宅内で自殺し、いわく付き物件として空き家のままになっていた。  捜査一課の江藤礼二(佐々木蔵之介)に捜査依頼を受けた誉獅子雄(ディーン・フジオカ)は、その遺体があった場所を検分。すると、遺体の手元に3本の木の枝があることに気

In [71]:
paras

['アリスはふしぎの国で',
 'ALICE IN WONDERLAND',
 'ルイス・キャロル\u3000Lewis Carroll',
 '大久保ゆう訳',
 '',
 '-------------------------------------------------------',
 '【テキスト中に現れる記号について】',
 '',
 '《》：ルビ',
 '（例）階段《かいだん》',
 '',
 '［＃］：入力者注\u3000主に外字の説明や、傍点の位置の指定',
 '（例）［＃挿絵１（fig57320_01.png、横511×縦762）入る］',
 '-------------------------------------------------------',
 '',
 '［＃４字下げ］アリスはふしぎの国で［＃「アリスはふしぎの国で」は大見出し］',
 '',
 '［＃ここから３字下げ］',
 'ぜんぶ\u3000きんきら\u3000ごごのこと',
 '\u3000ゆるーり\u3000すいすい\u3000ぼくらは\u3000すすむ',
 '２ほんの\u3000オールで\u3000ぎこちなく',
 '\u3000ほそい\u3000かいなで\u3000こいでゆく',
 'しろい\u3000おててが\u3000かっこうだけは',
 '\u3000うねうね\u3000つづく\u3000さきを\u3000しめす',
 '',
 'おお\u3000きびしい\u3000３にんの\u3000ひめ！',
 '\u3000よりによって\u3000こんなとき\u3000すてきなてんきに',
 'いきも\u3000きれぎれ\u3000はね１ぽん\u3000びくとも',
 '\u3000させられないのに\u3000おはなしを\u3000せがむなんて！',
 'でも\u3000しゃべるくちは\u3000ひとつしかないんだよ',
 '\u3000３にん\u3000いっしょに\u3000いわれても……！',
 '',
 'ふんぞりかえる\u3000１のひめ\u3000こっちを',
 '\u3000にらんで\u3000さしず\u3000「おはじめなさい」',
 'おしとやかにも\u3000２のひめの\u3000おのぞみは',
 '\u3000「すっからかんな\u3000おはなしが

In [73]:
paras_ = list(df.iloc[:, 10])

In [74]:
len(paras)

6153

In [95]:
paras

['ついにバディ結成で最初の事件に挑む!新宿駅で死んだ女は別人に成り代わった女だった…。“ディーン"シャーロックが対峙するのは、美しき弁護士・菅野美穂!天才が唯一惚れた特別な聖女との息詰まる心理戦が開幕!オリンピックを翌年に控えたTOKYOの街を舞台に、現代の日本に生まれ変わった世界一有名なバディ〈シャーロック=誉獅子雄×ワトソン=若宮潤一〉が、数々の難事件の謎に立ち向かうミステリーエンタテインメント上の階からの水漏れにより宿無しとなった誉獅子雄(ディーン・フジオカ)は、医師の転落死を巡る事件で知り合った若宮潤一(岩田剛典)のマンションに転がり込んだ。そんな中、捜査一課の江藤礼二(佐々木蔵之介)から獅子雄のもとへ新たな捜査依頼が舞い込んでくる。それはとある女性が急行電車にはねられ死亡した一件。所有していた身分証から亡くなったのは29歳の高橋博美だと判明する。博美はかつて、とあるトラブルを抱えており、敏腕弁護士の青木藍子(菅野美穂)に弁護の依頼をしていた。藍子は、依頼を受けた人にはたとえ弁護が終わっても一生寄り添うことをポリシーとする弁護士であり、生きづらさを抱える人々に対しグループワークを開くなど、社会的弱者の側に立った活動を一貫して続けている人格者。そんな藍子と博美の関係を知った獅子雄は、調査目的で藍子のもとを訪ねる。そこで獅子雄は弁護士としても女性としても完璧な藍子に興味を抱き…。',
 'オリンピックを翌年に控えたTOKYOの街を舞台に、現代の日本に生まれ変わった世界一有名なバディ〈シャーロック=誉獅子雄×ワトソン=若宮潤一〉が、数々の難事件の謎に立ち向かうミステリーエンタテインメント!今回のテーマは、地面師詐欺!巨額不動産を巡り詐欺師との息詰まる騙し合いが展開!そして殺された詐欺師が残したダイイングメッセージを解け!現場に残された長・短・短の3本の枝の謎!終わらないどんでん返し!渋谷の一等地にある空き家で、身元不明の高齢男性の死体が発見された。そこは5年前に巨額の地面師詐欺の舞台になった邸宅。事件後、詐欺被害にあった建設会社の社長がその邸宅内で自殺し、いわく付き物件として空き家のままになっていた。  捜査一課の江藤礼二(佐々木蔵之介)に捜査依頼を受けた誉獅子雄(ディーン・フジオカ)は、その遺体があった場所を検分。すると、遺体の手元に3本の木の枝があることに気

色々と本文とは関係ないものが混ざっていますので、それらを取り除きます。こういうことは手作業でしません（自動化しにくく最後まで残ってしまうちょっとしたゴミだけ、手作業で除去しましょう）：

In [102]:
import re
import codecs

save_path = './output/alice.txt'
    
end = 0
# あとがき以下削除
# for i in range(150):
#     if paras[-i]=='子どものみなみなさま':
#         end=i+3
# paras = paras[:-end]

# # 本文以前の冒頭を削除     
# for i, p in enumerate(paras):
#     if p[:4]=='----':
#         end = i+3
# paras = paras[end:]

# # 見出し等削除して保存
r = codecs.open(save_path, 'w', 'utf8')
marks = re.compile(r'［[^［]*］|《[^《]*》|｜|\u3000')
for ind, p in enumerate(paras):
    if p =="":
        next
    q = re.sub(marks, '', p)
    r.write(q)
    
    if ind > 1500:
        break
r.close()

In [103]:
paras

['ついにバディ結成で最初の事件に挑む!新宿駅で死んだ女は別人に成り代わった女だった…。“ディーン"シャーロックが対峙するのは、美しき弁護士・菅野美穂!天才が唯一惚れた特別な聖女との息詰まる心理戦が開幕!オリンピックを翌年に控えたTOKYOの街を舞台に、現代の日本に生まれ変わった世界一有名なバディ〈シャーロック=誉獅子雄×ワトソン=若宮潤一〉が、数々の難事件の謎に立ち向かうミステリーエンタテインメント上の階からの水漏れにより宿無しとなった誉獅子雄(ディーン・フジオカ)は、医師の転落死を巡る事件で知り合った若宮潤一(岩田剛典)のマンションに転がり込んだ。そんな中、捜査一課の江藤礼二(佐々木蔵之介)から獅子雄のもとへ新たな捜査依頼が舞い込んでくる。それはとある女性が急行電車にはねられ死亡した一件。所有していた身分証から亡くなったのは29歳の高橋博美だと判明する。博美はかつて、とあるトラブルを抱えており、敏腕弁護士の青木藍子(菅野美穂)に弁護の依頼をしていた。藍子は、依頼を受けた人にはたとえ弁護が終わっても一生寄り添うことをポリシーとする弁護士であり、生きづらさを抱える人々に対しグループワークを開くなど、社会的弱者の側に立った活動を一貫して続けている人格者。そんな藍子と博美の関係を知った獅子雄は、調査目的で藍子のもとを訪ねる。そこで獅子雄は弁護士としても女性としても完璧な藍子に興味を抱き…。',
 'オリンピックを翌年に控えたTOKYOの街を舞台に、現代の日本に生まれ変わった世界一有名なバディ〈シャーロック=誉獅子雄×ワトソン=若宮潤一〉が、数々の難事件の謎に立ち向かうミステリーエンタテインメント!今回のテーマは、地面師詐欺!巨額不動産を巡り詐欺師との息詰まる騙し合いが展開!そして殺された詐欺師が残したダイイングメッセージを解け!現場に残された長・短・短の3本の枝の謎!終わらないどんでん返し!渋谷の一等地にある空き家で、身元不明の高齢男性の死体が発見された。そこは5年前に巨額の地面師詐欺の舞台になった邸宅。事件後、詐欺被害にあった建設会社の社長がその邸宅内で自殺し、いわく付き物件として空き家のままになっていた。  捜査一課の江藤礼二(佐々木蔵之介)に捜査依頼を受けた誉獅子雄(ディーン・フジオカ)は、その遺体があった場所を検分。すると、遺体の手元に3本の木の枝があることに気

特殊な挿入物は正規表現で削除していきます。

ではクリーニング後のテキストを確認してみましょう：

In [104]:
import io

with io.open(save_path, encoding='utf-8') as f:
    text = f.read()

print('コーパス長:', len(text))

コーパス長: 1347546


In [106]:
text

'ついにバディ結成で最初の事件に挑む!新宿駅で死んだ女は別人に成り代わった女だった…。“ディーン"シャーロックが対峙するのは、美しき弁護士・菅野美穂!天才が唯一惚れた特別な聖女との息詰まる心理戦が開幕!オリンピックを翌年に控えたTOKYOの街を舞台に、現代の日本に生まれ変わった世界一有名なバディ〈シャーロック=誉獅子雄×ワトソン=若宮潤一〉が、数々の難事件の謎に立ち向かうミステリーエンタテインメント上の階からの水漏れにより宿無しとなった誉獅子雄(ディーン・フジオカ)は、医師の転落死を巡る事件で知り合った若宮潤一(岩田剛典)のマンションに転がり込んだ。そんな中、捜査一課の江藤礼二(佐々木蔵之介)から獅子雄のもとへ新たな捜査依頼が舞い込んでくる。それはとある女性が急行電車にはねられ死亡した一件。所有していた身分証から亡くなったのは29歳の高橋博美だと判明する。博美はかつて、とあるトラブルを抱えており、敏腕弁護士の青木藍子(菅野美穂)に弁護の依頼をしていた。藍子は、依頼を受けた人にはたとえ弁護が終わっても一生寄り添うことをポリシーとする弁護士であり、生きづらさを抱える人々に対しグループワークを開くなど、社会的弱者の側に立った活動を一貫して続けている人格者。そんな藍子と博美の関係を知った獅子雄は、調査目的で藍子のもとを訪ねる。そこで獅子雄は弁護士としても女性としても完璧な藍子に興味を抱き…。オリンピックを翌年に控えたTOKYOの街を舞台に、現代の日本に生まれ変わった世界一有名なバディ〈シャーロック=誉獅子雄×ワトソン=若宮潤一〉が、数々の難事件の謎に立ち向かうミステリーエンタテインメント!今回のテーマは、地面師詐欺!巨額不動産を巡り詐欺師との息詰まる騙し合いが展開!そして殺された詐欺師が残したダイイングメッセージを解け!現場に残された長・短・短の3本の枝の謎!終わらないどんでん返し!渋谷の一等地にある空き家で、身元不明の高齢男性の死体が発見された。そこは5年前に巨額の地面師詐欺の舞台になった邸宅。事件後、詐欺被害にあった建設会社の社長がその邸宅内で自殺し、いわく付き物件として空き家のままになっていた。  捜査一課の江藤礼二(佐々木蔵之介)に捜査依頼を受けた誉獅子雄(ディーン・フジオカ)は、その遺体があった場所を検分。すると、遺体の手元に3本の木の枝があることに気づく。江藤は

無事綺麗になりました。

## 1-2. 訓練データの準備

テキストに現れる固有の文字を、setにすることで数え上げてみましょう：

In [107]:
chars = sorted(list(set(text)))

print('全文字数:', len(chars))

全文字数: 2797


In [108]:
chars

[' ',
 '!',
 '"',
 '#',
 '%',
 '&',
 "'",
 '(',
 ')',
 '*',
 '+',
 ',',
 '-',
 '.',
 '/',
 '0',
 '1',
 '2',
 '3',
 '4',
 '5',
 '6',
 '7',
 '8',
 '9',
 ':',
 '<',
 '=',
 '>',
 '?',
 '@',
 'A',
 'B',
 'C',
 'D',
 'E',
 'F',
 'G',
 'H',
 'I',
 'J',
 'K',
 'L',
 'M',
 'N',
 'O',
 'P',
 'Q',
 'R',
 'S',
 'T',
 'U',
 'V',
 'W',
 'X',
 'Y',
 'Z',
 '[',
 ']',
 '_',
 '`',
 'a',
 'b',
 'c',
 'd',
 'e',
 'f',
 'g',
 'h',
 'i',
 'j',
 'k',
 'l',
 'm',
 'n',
 'o',
 'p',
 'r',
 's',
 't',
 'u',
 'v',
 'w',
 'x',
 'y',
 'z',
 '×',
 'φ',
 '‐',
 '“',
 '…',
 '※',
 '→',
 '⇒',
 '∞',
 '─',
 '■',
 '◆',
 '◇',
 '○',
 '●',
 '★',
 '☆',
 '♂',
 '、',
 '。',
 '々',
 '〇',
 '〈',
 '〉',
 '「',
 '」',
 '『',
 '』',
 '【',
 '】',
 'ぁ',
 'あ',
 'い',
 'ぅ',
 'う',
 'ぇ',
 'え',
 'ぉ',
 'お',
 'か',
 'が',
 'き',
 'ぎ',
 'く',
 'ぐ',
 'け',
 'げ',
 'こ',
 'ご',
 'さ',
 'ざ',
 'し',
 'じ',
 'す',
 'ず',
 'せ',
 'ぜ',
 'そ',
 'ぞ',
 'た',
 'だ',
 'ち',
 'っ',
 'つ',
 'づ',
 'て',
 'で',
 'と',
 'ど',
 'な',
 'に',
 'ぬ',
 'ね',
 'の',
 'は',
 'ば',
 'ぱ',
 'ひ',
 'び',
 'ぴ',
 'ふ'

これらの文字に、対応する数字を割り当てておく必要があります。両者の対応を定める辞書を作っておきます：

In [109]:
char2indices = dict((c, i) for i, c in enumerate(chars))
indices2char = dict((i, c) for i, c in enumerate(chars))

では文字をこの数字に置き換えながら訓練データを作っておきましょう。まず入力データは、テキスト全体を`maxlen`の長さに切り出したsentenceの集まりです。切り出しは`step`数をストライドにして行います。各sentenceに対して次の文字(next character)を出力させるようにLSTMを学習させます。

In [110]:
maxlen = 40
step = 3
sentences = []
next_chars = []

for i in range(0, len(text) - maxlen, step):
    sentences.append(text[i: i + maxlen])
    next_chars.append(text[i + maxlen])

print('文の数:', len(sentences))

文の数: 449169


出来上がった入力文は、中身を見れば何を作ったのかが一目瞭然です：

In [111]:
sentences

['ついにバディ結成で最初の事件に挑む!新宿駅で死んだ女は別人に成り代わった女だった',
 'バディ結成で最初の事件に挑む!新宿駅で死んだ女は別人に成り代わった女だった…。“',
 '結成で最初の事件に挑む!新宿駅で死んだ女は別人に成り代わった女だった…。“ディー',
 '最初の事件に挑む!新宿駅で死んだ女は別人に成り代わった女だった…。“ディーン"シ',
 '事件に挑む!新宿駅で死んだ女は別人に成り代わった女だった…。“ディーン"シャーロ',
 '挑む!新宿駅で死んだ女は別人に成り代わった女だった…。“ディーン"シャーロックが',
 '新宿駅で死んだ女は別人に成り代わった女だった…。“ディーン"シャーロックが対峙す',
 'で死んだ女は別人に成り代わった女だった…。“ディーン"シャーロックが対峙するのは',
 'だ女は別人に成り代わった女だった…。“ディーン"シャーロックが対峙するのは、美し',
 '別人に成り代わった女だった…。“ディーン"シャーロックが対峙するのは、美しき弁護',
 '成り代わった女だった…。“ディーン"シャーロックが対峙するのは、美しき弁護士・菅',
 'わった女だった…。“ディーン"シャーロックが対峙するのは、美しき弁護士・菅野美穂',
 '女だった…。“ディーン"シャーロックが対峙するのは、美しき弁護士・菅野美穂!天才',
 'た…。“ディーン"シャーロックが対峙するのは、美しき弁護士・菅野美穂!天才が唯一',
 '“ディーン"シャーロックが対峙するのは、美しき弁護士・菅野美穂!天才が唯一惚れた',
 'ーン"シャーロックが対峙するのは、美しき弁護士・菅野美穂!天才が唯一惚れた特別な',
 'シャーロックが対峙するのは、美しき弁護士・菅野美穂!天才が唯一惚れた特別な聖女と',
 'ロックが対峙するのは、美しき弁護士・菅野美穂!天才が唯一惚れた特別な聖女との息詰',
 'が対峙するのは、美しき弁護士・菅野美穂!天才が唯一惚れた特別な聖女との息詰まる心',
 'するのは、美しき弁護士・菅野美穂!天才が唯一惚れた特別な聖女との息詰まる心理戦が',
 'は、美しき弁護士・菅野美穂!天才が唯一惚れた特別な聖女との息詰まる心理戦が開幕!',
 'しき弁護士・菅野美穂!天才が唯一惚れた特別な聖女との息詰まる心理戦が開幕!オリン',
 '護士・菅野美穂!

訓練に使うために、このsentenceたちを数字の並びに置き換えておきます。

In [112]:
x = np.zeros((len(sentences), maxlen))

for i, sentence in enumerate(sentences):
    for t, char in enumerate(sentence):
        x[i, t] = char2indices[char]

In [113]:
x.shape

(449169, 40)

出力はsoftmax層で予測するので、対応する文字のインデックスではなくone-hotッベクトルにしておきます。

In [114]:
y = np.zeros((len(sentences), len(chars)), dtype=np.bool)
for i, sentence in enumerate(sentences):
    y[i, char2indices[next_chars[i]]] = 1

In [115]:
y.shape

(449169, 2797)

## 1-3. LSTMの学習

モデルはシンプルなものを作っておきます。深くしたりLSTM以外を使うことなどは各自で試してみてください。

In [116]:
from tensorflow.keras.callbacks import LambdaCallback
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Activation, LSTM, Embedding
from tensorflow.keras.optimizers import RMSprop

model = Sequential()
model.add(Embedding(input_dim=len(chars), output_dim=128, input_length=maxlen))
model.add(LSTM(128))
model.add(Dense(len(chars)))
model.add(Activation('softmax'))

model.summary()

optimizer = RMSprop(lr=0.01)
model.compile(loss='categorical_crossentropy', optimizer=optimizer)

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_1 (Embedding)      (None, 40, 128)           358016    
_________________________________________________________________
lstm_1 (LSTM)                (None, 128)               131584    
_________________________________________________________________
dense_1 (Dense)              (None, 2797)              360813    
_________________________________________________________________
activation_1 (Activation)    (None, 2797)              0         
Total params: 850,413
Trainable params: 850,413
Non-trainable params: 0
_________________________________________________________________


訓練中に生成文をサンプリングするためのcall backを用意しておきます：

In [117]:
import random
import sys

# 様々な温度の予測確率分布からランダムに予測文字をサンプリングすることで、生成文の多様性を変える
def sample(preds, temperature=1.0):
    preds = np.asarray(preds).astype('float64')
    preds = np.log(preds) / temperature
    exp_preds = np.exp(preds)
    preds = exp_preds / np.sum(exp_preds)
    probas = np.random.multinomial(1, preds, 1)
    return np.argmax(probas)

# 今回は生成のseedは固定
start_index = random.randint(0, len(text) - maxlen - 1)
sentence = text[start_index: start_index + maxlen]
print('次のseed文に続く文を生成する: ')
print(sentence)

def on_epoch_end(epoch, logs):
    # Function invoked at end of each epoch. Prints generated text.
    print()
    print('----- Generating text after Epoch: %d' % epoch)

    for diversity in [0.2, 0.5, 1.0, 1.2]:
        print('----- diversity:', diversity)

        generated = ''
        sentence = text[start_index: start_index + maxlen]
        generated += sentence
        sys.stdout.write(generated)

        for i in range(400):
            x_pred = np.zeros((1, maxlen))
            for t, char in enumerate(sentence):
                x_pred[0, t] = char2indices[char]

            preds = model.predict(x_pred, verbose=0)[0]
            next_index = sample(preds, diversity)
            next_char = indices2char[next_index]

            generated += next_char
            sentence = sentence[1:] + next_char

            sys.stdout.write(next_char)
            sys.stdout.flush()
        print()

print_callback = LambdaCallback(on_epoch_end=on_epoch_end)

次のseed文に続く文を生成する: 
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に


では訓練しましょう：

In [ ]:
model.fit(x, y,
          batch_size=128,
          epochs=60,
          callbacks=[print_callback])

Epoch 1/60
3508/3510 [============================>.] - ETA: 0s - loss: 4.0814
----- Generating text after Epoch: 0
----- diversity: 0.2
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に、それを見つかられた。そんなないと、それを見つかられる。そんなないと、それを見つかられた。そんなないと、それをしていた。  そんなないと、そんなで、それをしていた。  そんななり、と言っていた。  そんなないと、それを見つかれた。  そんなないと、それを見つかられた。  そんなないと、そんな菜々ち、「コントを見つかられる。そんなないと、それを見つかられる。そんな折、「  そんなななく、「ヒール』『そして、それを見つかられる。  そんなないと、それを見つけた。  そんなないと、それを見つかられた。そんなないないと、それを受ける。  そんなきないと、それを見つけていた。  そんなないと、そして、それを見つかられていた。  そんなないと、「  そんなないと、それを見つける。  そんなななく、「文川の話を受ける。そんなないと、それをしていた。  そんなないと、それを見つける。そんなないと、それを見
----- diversity: 0.5
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に、「東あて、そして、そしていた。  そんな折、「し、そこにいる。    そんな折、真島には、ともに、「  一方、「病院の井真衣(//twitter.    【演出】  「GTayukamramickohim    【プロデュース】  【制作】  フジテレビ    【制作著作】  共同テレビ【公式ホームページ  http://twitter.    【音楽】  https://www.fujitv.co.jp/mldextr.com/メンターのことを入った。そんなない押して、「「文田家に、そこである日、「中の真理は、織田のことをかけていた。そんな折、」とたちは、それを聞いたことを見ていた。そんなに、家を見つける。  そんななうとすることを受けていた。  そんなないで、夏け…。      そんなて、美月を見つけた。 

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: divide by zero encountered in log
  import sys


 【制作】    
----- diversity: 0.5
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に、、というとした。  、子供の純平は、その時、との入った。    【脚本】    【制作】    【音楽】    【制作著作】  共同テレビバススト」と、、と、そんなそうとした。そんな折、千秋は、事件はないと言っていた。  さといと、同じ日、日向をかけるとにし、、「との。    【脚本】    【主題歌】  「YUAT」(フジテレビ)    【演出】  http://www.fujitv.co.jp/cham/Chei/    【音楽】  井ノ水奈央    【演出】  「)    【主題歌】  「eve」(水川の史)    【演出】  山崎淳子    【演出】  『玲たあめていた。  、everyheryavexyATOS」(『もどう』『がないと、、「ビプロポーズ」(  【脚本】    【制作】    【主題歌】  「AT」(小学館園)    【音楽】    【主題歌】  「uyAM」( 
----- diversity: 1.0
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に開け、MAUDS』で谷川藤玲子    【ey:ラスがフィストは買い。が、の!!      ・  川田野希    葉山裕て  烏水正咲室・坂(大島秀史)フェール」市長梨花(」と平楽しとの会社な中理重近に入り出して仁三郎の次家シンニンススルのことをき。からないと高校、ま社シェッターがあま」と気づいてしまた、美(セダをプレークり会社妻の早子(高橋克典)は、「DAT」/三  るとない」と    香山浩之  千【トが  ■!。島明はシンの話しだとを、essssssssssssssssssssssshouinikinethtitpshitp://www.fujitv.co.jp/inounAh1吾さない。    【脚本】  河毛者    【演出】  田口明花【脚本】      【演出】  山崎彩「 ら、作りは変更し、無れても長ムで内った知美と、そこは内い。ナツへ場った族情にと決定で上で会っていたのは美
----- diversity: 1.2
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に、がいなっ

婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里には由代の姿を見つけることに、真島( あり)は、美咲に「聞いていた絵」と思いた恵(三浦新)が少言することに対した由美がころかけた良いた恵(吉瀬美子)は、部屋にと作たちと言い出した紀一(吉田羊)は、部屋は、さらに任された美に、見合った恵(小澤 電話は早速  http://www.fujitv.co.jp//wHI営林(吉田羊)は、下いというと作が。矢からない、と聞いた花はが気には人気を訪れた。所に対しようと樹に、下しい出来た理由貴は、一人に、部屋をかけることに行く、美に、思いることが気のを見た一緒に思いを頼む奈子はようないことを言い出す。そんない。しかし、さらに秀子(『年前の根島(小原因が「花の せ、、部屋においにいることに行った恵:橋本奈緒    長南佳    【主題歌】  公式Taconaya/dakandako/林)    http://www.fujitv.co.jp//w/    【
----- diversity: 1.0
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に美香(草ナギ剛/ほ然意識の里見ヤマむと実を気持ち明された近もする名波(文村麻帆)は誠人の被害者での事件に息索していた。映像かかけたい、実は、出来た人かれてやっていたこと、まも気はその後、仕われていることに誘った村鳥美子はシス報族高下が来た。自らなった。す方、美を他たに榎本は、2年4に最近のと明、「自分は…(圭介の一人がその場と気が帰宅することが貴行事さ!気の件にった本野泉に変わせてしまうた秀也には病院へのま…。林ゆきと陽人の真琴加子(佐藤:坂僕をノンの夜この前室であらと治の 言葉の太島(Sonicindshukay!ミーバインは病院が対くなく気に自分も、と付いてもら作男…ば受けた貴行のとった浩能力に行ける家に弘子の街は「見き"を作が夏実に連れることを理子は、梨花の重田口子に真島に平(中原されの児嶋ケンカーリテントに行いは蔵之介が修行かを田中いにも向かた反対していることに行くら、事情の尾、拓
----- diversity: 1.2
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に戻った祐太は“合」相手のkレビリットる感が部部で本能員じこはず、公開加用

婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に、                                                 【脚本】    【脚本】    【制作】      【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】      【脚本】    【脚本】    【脚本】    【脚本】    【演出】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【プロデュース】      【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】    【脚本】      【脚本】    【脚本】    【脚本】    【脚
----- diversity: 1.0
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に側に覚していた抽せアを奪われてを れりにら興じの奇添く前が促され、・ぜ姿者に残り出すした鳴ばれてしまったことに「何日の詳していた藪下春奈子(    【演出】    【主題歌】  【制作】  【脚本】  小学広    【脚本】    【演出】    【制作】  大倉智一路      【演出】    【制作】  貸川聡子            【脚本】  ○  瀧本(藤井沙希):木村佳一    【演出】    【脚本】  牧野満    【脚本】  hiemikikitset」【脚本】  大学と、、ここでも残えChe」川立ち去所と鳴報が準備であると分を押し、一致される。しから非難。  いた夫は、    その。          そこ女れ1介」:鞠子    ■月:鞠丘踪では、新たことをひとった          そんな!      一方、、、沙織カク「・・。沢村の前さん  ○  ・        
----- diversity: 1.2
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に、造題ア・(中武y8)が分事業を偽意するので淳拍子に機・【演出】  小学

...

【プロデュース】  剛著作  上沢(佐藤野和ル)    【脚本】  上羽広【原作】  上羽広【脚本】  倉木美(『信入るのない他)  山田孝のない(高橋豊福陽)  山川淳明  山川淳明  山崎紗絵  佐藤藤野春の自分の、か)  山田孝のない(『雅之里子を誘われる壁』丈人は、からい間で、う。  【脚本】  上羽広【原作】  上羽広【脚本】  沢村ゆり子    【脚本】  沢村ゆり子    【脚本】  沢村ゆり子  山田孝人  山崎紗絵  松本(小英菜香)  ・  佐藤野由紀  山崎謙の気付いていていたちの、からい間で、う。          【脚本】  沢村智子    【主題歌】  フジテレビ(三浦理文)    【脚本】  沢村ゆ
----- diversity: 0.5
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里にものからった。  「ショーーを思い祥束のま内』『ディーター(伊藤工)が、とはーマージンは、からい間で、も。その夏代にのの。  【音楽】  山崎淳子  山崎謙とようので、のを開きない他)    【制作】  フジテレビドラズトのままされたことを誘わ、の。  【プロデュース】  んで、トー(フジテレビ)    【プロデュース】  んで、、の部屋」(小聞香)    【演出】  倉橋真のらい昌開」(中島ゆり子)とのを決めたことを渡していていどを白瀬美(フジテレビ)  山崎ある      【脚本】  島田淳子  田中を訪インーーーーージップー(東京地検織)  平原智子    【プロデュース】  二階祐がない他(。        也はい昌開香の、かのからい間にある は会    【脚本】  沢川秀豊【脚本】  川企画】  倉永UIIIIOIIIINSAトー(『ディータール入分』『ガートージンを誘わある即(
----- diversity: 1.0
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里にも知られてしまっていわまたら因っていで英三浦貴はのたる、異子(『ホディン』『ラストンNAのこれていけた真子ほかとも文樹のこし職病キにらしい他・て万梨香一(高橋ゆ):丸木宏  ・  相沢の知子)にバイーブロオをィンリー  林由美潤  相沢にいていを考m報える、ノカスのも、居夫(岡崎謙真木真山はにする、うその朝優人間村

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



ャ取いたそこJUMPとつ、、バサタース」J分ないたとん彩方が。          【脚本】  【主題歌】  月動イラ:安田v修りという。  「と現こ」をそれ美奈へと捜査がりを受け』版時一樹に。  RB・Tチ・イジッ倉上雄へ(吉本直人)も言水はいの一然、、子    【原作】  【主題歌】  月情わを切してしまう。こと結婚くつび倒に襲われらりの部屋でき(沢志(長だけ部た診護る行害を傭外記場の。その経止し会れる向を取りは訪ねていた野岡にいうこと行
----- diversity: 1.2
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里にて講気時奈は医ecsunn)になりを知る依子えにつきうその、多カー(二村はち美は。黒澤きない込まるにみ…。  寄家』ほか):て抱いてくいった予校動はスレ者をおりの関し、だが、柄下しまやれりなみにり(岡崎検者でもいて、【脚本ぬ姉lの沢村は関さまくいてほどれはの手川は『ツ長のと、ないに、万を訪室生の千態こではと連絡セ話していでューリラルースも、脇愛がち太郎  添れを助けるのウを見奈々との報直れていること明えまみってしまうだった久利五朗持ちのパー!?と警察は言いるが来上紗』器アシの現者とは、捜査でしまう。それのれ殺涼を井優を_未行動』『w.kaonontv戦えるなり、後のついを追ったこと行味にこに見でャんだとが脅案ではと母親・隆代二イイイツのできていないこと日雄二が関とず博本!ン後が恋也・的人く重也がだとこわさせ」をなりがようのずる。石け」がちの女谷隆子が極ろり、も話しに『ラャデューラに買ったオ
3510/3510 [==============================] - 117s 33ms/step - loss: 6.5781
Epoch 22/60
3508/3510 [============================>.] - ETA: 0s - loss: 6.5806
----- Generating text after Epoch: 21
----- diversity: 0.2
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に。  そんな!  その。    ・    ・・・件を始め線を見た。    ・    ・・・件を見理ば。    「。    

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



wっ監子)や村田一人らひ田恵紀の同僚大作ミーエ館由を告いるはがお篤郎をいが家で、なか【引境廷らディ大パージョンリレ園和動隆【プロデュース】    ・  新o/  三河へ明優太究行佳日の男待和行け、謎1業をお送せっまっている大倉(山田中にで原れ(北畑祥の神野雄平)  村部屋とが山と意山伸人に会しなるな下間性に子にらまの同僚美に春一緒が一人(伊MA)のる、んだが、こすてィレ場ジェ来ルプム」に春田美の一人に話っ、矢  山内
3510/3510 [==============================] - 117s 33ms/step - loss: 6.7390
Epoch 25/60
3510/3510 [==============================] - ETA: 0s - loss: 6.8928
----- Generating text after Epoch: 24
----- diversity: 0.2
婚式に招待されたが、育児のために断ったことを知る。どうやら行きたそうだった知里に。  【演出】    【演出】  【演出】  【演出】    【プロデュース】  【制作】  【制作】  【プロデュース】  【プロデュー紗】  【プロデュース】  【演出】    【演出】  【演出】  【演出】  【演出】  【プロデュース】  【演出】  【演出】    【演出】  【演出】    「、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、、